In [20]:
pip install pandas-profiling

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 328.7/328.7 kB 28.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.7/102.7 kB 1.5 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 21.1 MB/s eta 0:00:00:00:01
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 679.5/679.5 kB 14.0 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.7/4.7 MB 55.9 MB/s eta 0:00:00:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 52.5 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27082 sha256=c30e06dd943575a2cda70bb01888a718b52b4e6d3f427fbae7cc3e6ac1ae377d
  Stored in directory: /home/ec2-user/.cache/pip/wheels/ea/1c/a8/5cec3479cd45136a7111e2d96aac299b219b199c411665250b
Successfully built htmlmin
Note: you may need to restart the kernel to use updated packages.


In [22]:
import boto3
import pandas as pd; pd.set_option('display.max_column', 100)
import numpy as np
import matplotlib.pyplot as plt
import pandas_profiling as pp

from sklearn.model_selection import train_test_split

from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import roc_curve, classification_report

## define bucket in which you are trying to reach
s3 = boto3.resource('s3')
bucket_name = 'daltondencklau-data445-bucket'
bucket = s3.Bucket(bucket_name)

## define csv file to read in the bucket
file_key= 'train.csv'

## syntax to allow us to read the file
bucket_object = bucket.Object(file_key)
file_object = bucket_object.get()
file_content_stream = file_object.get('Body')

## reading the training data file
train = pd.read_csv(file_content_stream, sep = '|')
train.head()

trustLevel  totalScanTimeInSeconds  grandTotal  lineItemVoids  \
0           5                    1054       54.70              7   
1           3                     108       27.36              5   
2           3                    1516       62.16              3   
3           6                    1791       92.31              8   
4           5                     430       81.53              3   

   scansWithoutRegistration  quantityModifications  scannedLineItemsPerSecond  \
0                         0                      3                   0.027514   
1                         2                      4                   0.129630   
2                        10                      5                   0.008575   
3                         4                      4                   0.016192   
4                         7                      2                   0.062791   

   valuePerSecond  lineItemVoidsPerPosition  fraud  
0        0.051898                  0.241379      0  
1        0.253333                  0.357143      0  
2        0.041003                  0.230769      0  
3        0.051541                  0.275862      0  
4        0.189605                  0.111111      0

In [2]:
## retreiving the testing dataset

## define csv file to read in the bucket
file_key= 'test.csv'

## syntax to allow us to read the file
bucket_object = bucket.Object(file_key)
file_object = bucket_object.get()
file_content_stream = file_object.get('Body')

## reading the data file
test = pd.read_csv(file_content_stream, sep = '|')
test.head()

trustLevel  totalScanTimeInSeconds  grandTotal  lineItemVoids  \
0           4                     467       88.48              4   
1           3                    1004       58.99              7   
2           1                     162       14.00              4   
3           5                     532       84.79              9   
4           5                     890       42.16              4   

   scansWithoutRegistration  quantityModifications  scannedLineItemsPerSecond  \
0                         8                      4                   0.014989   
1                         6                      1                   0.026892   
2                         5                      4                   0.006173   
3                         3                      4                   0.026316   
4                         0                      0                   0.021348   

   valuePerSecond  lineItemVoidsPerPosition  
0        0.189465                  0.571429  
1        0.058755                  0.259259  
2        0.086420                  4.000000  
3        0.159380                  0.642857  
4        0.047371                  0.210526

The data (including feature names and feature inputs) were all in one column. I used the sep = '|' to separate the data and put them into their own columns.

### Target Variable Analysis
***

In [4]:
## reporting the number of observations in training dataset
train.shape

(1879, 10)

In [5]:
## reporting the number of observations in testing dataset
test.shape

(498121, 9)

In [6]:
## creating frequency table for target variable (fraud)
train['fraud'].value_counts() / train.shape[0]

0    0.944651
1    0.055349
Name: fraud, dtype: float64

Only 5.5% of the training dataset contains features where fraud = 0. I will have to stratify the Y variable when I build models to avoid under or over fitting.

### Visualizations: Pandas Profiling
***

In [24]:
## creating visualization for target variable
profile = pp.ProfileReport(train, title="EDA", explorative=True)

## printing using HTML
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

EXPLAIN visuals